# core

> Fill in a module description here

In [ ]:
#| default_exp core

In [ ]:
#| hide
from nbdev.showdoc import *

In [ ]:
#| export
import gradio as gr
from Levenshtein import ratio
import json
import xml.etree.ElementTree as ET
from tqdm import tqdm

In [ ]:
#| export
class ApiClient:


    def __init__(self, data_path: str):
        DATA_PATH = data_path

        with open(DATA_PATH, "r", encoding="utf-8") as f:
            documents_data = json.load(f)

        self.documents_data = documents_data

    def extract_text_from_lines(self, element):
        """本文タイプの要素からテキストを抽出する"""
        lines = element.findall(".//*[@type='本文']")
        return ''.join(line.text for line in lines)

    def format_prediction_result(self, result):
        """予測結果を 'vol-page' 形式にフォーマットする"""
        first_result = result[0]
        return f'{first_result["vol"]}-{first_result["page"]}'


    def search_similar_texts(self, query, selected_vols, top_n=5, xml_file_path=None):
        """テキストの類似検索を実行する関数

        Args:
            query (str): 検索クエリテキスト
            selected_vols (list): 検索対象の巻のリスト
            top_n (int, optional): 返す結果の数. デフォルトは5
            xml_file (gradio.File, optional): 比較対象のXMLファイル

        Returns:
            list: 検索結果のリスト。XMLファイル処理時は[predict_results]、
                通常検索時は[top_results]を返す
        """
        if xml_file_path is not None:
            
            try:
                with open(xml_file_path, "r", encoding="utf-8") as f:
                    xml_str = f.read()
                    
                root = ET.fromstring(xml_str)
                
                # ページ要素の取得
                elements = root.findall(".//*[@type='page']")

                # 予測実行
                predict_results = {}
                for i, element in tqdm(enumerate(elements, 1)):
                    text = self.extract_text_from_lines(element)
                    top_results = self.predict(text, selected_vols, 1)
                    predict_results[str(i)] = self.format_prediction_result(top_results)

                return [predict_results]
        
            except (ET.ParseError, FileNotFoundError, PermissionError) as e:
                print(f"XMLファイルの処理中にエラーが発生しました: {str(e)}")
                return [[], {}]
        

        top_results = self.predict(query, selected_vols, top_n)
        
        return [top_results] # , vol_percentages
        

    def predict(self, query, selected_vols, top_n=5):
        """テキストの類似度を計算し、上位の結果を返す

        Args:
            query (str): 検索クエリテキスト
            selected_vols (list): 検索対象の巻のリスト
            top_n (int, optional): 返す結果の数. デフォルトは5

        Returns:
            list: スコア順にソートされた上位n件の検索結果
        """
        results = []
        
        for doc in self.documents_data:
            # 選択された巻のみを検索対象とする
            if not selected_vols or str(doc["vol"]) in selected_vols:
                score = ratio(query, doc["text"])
                results.append({
                    "vol": doc["vol"],
                    "page": doc["page"],
                    "score": score,
                    "text": doc["text"]
                })

        results.sort(key=lambda x: x["score"], reverse=True)
        top_results = results[:top_n]  # top_nで指定された件数だけを取得

        return top_results

In [ ]:
#| hide
import nbdev; nbdev.nbdev_export()